#GANSPACE - Discovering Interpretable GAN Controls 

Using https://github.com/harskish/ganspace to find latent directions in a stylegan2 model. (This could easily be ported to other models, if anyone implements it please get in touch, and i'll add it to the notebook!)

Notebook put together by [@realmeatyhuman](https://twitter.com/realmeatyhuman)



In [0]:
#@title Mount Google Drive
from google.colab import drive
drive.mount('/content/drive/', force_remount=True)

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive/



## Setup
It's quite a long install - but if you hit play on all the cells below, everything should run smoothly. Go grab yourself a cup of tea.

1. Install anaconda or miniconda
2. Check conda env is working with `conda info --envs`

3b. Extra steps for colab - check GPU is connected with !nvidia-smi, then overwrite environment.yml file to use base colab environment

4. Install dependencies: `conda env update -f environment.yml --prune`
5. Setup submodules: `git submodule update --init --recursive`
6. Run command `python -c "import nltk; nltk.download('wordnet')"`

#### Linux
1. Install CUDA toolkit (match the version in environment.yml)
2. Download pycuda sources from: https://pypi.org/project/pycuda/#files
3. Extract files: `tar -xzf pycuda-VERSION.tar.gz`
4. Configure: `python configure.py --cuda-enable-gl --cuda-root=/path/to/cuda`
5. Compile and install: `make install`
6. Install Glumpy: `pip install setuptools cython glumpy`

### StyleGAN2
The bundled StyleGAN2 model requires additional setup steps due to the custom CUDA kernels involved.
1. Install CUDA toolkit (match the version in environment.yml)
2. On Windows: install and open 'x64 Native Tools Command Prompt for VS 2017'
3. `conda activate ganspace`
4. `cd models/stylegan2/stylegan2-pytorch/op`
5. `python setup.py install`
6. Test: `python -c "import torch; import upfirdn2d_op; import fused; print('OK')"`



In [0]:
#@title Install conda on colab
################################################################################
! wget https://repo.anaconda.com/miniconda/Miniconda3-py37_4.8.2-Linux-x86_64.sh
! chmod +x Miniconda3-py37_4.8.2-Linux-x86_64.sh
! bash ./Miniconda3-py37_4.8.2-Linux-x86_64.sh -b -f -p /usr/local
import sys
sys.path.append('/usr/local/lib/python3.7/site-packages/')

--2020-04-29 15:29:23--  https://repo.anaconda.com/miniconda/Miniconda3-py37_4.8.2-Linux-x86_64.sh
Resolving repo.anaconda.com (repo.anaconda.com)... 104.16.130.3, 104.16.131.3, 2606:4700::6810:8303, ...
Connecting to repo.anaconda.com (repo.anaconda.com)|104.16.130.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 85055499 (81M) [application/x-sh]
Saving to: ‘Miniconda3-py37_4.8.2-Linux-x86_64.sh’

Miniconda3-py37_4.8 100%[===================>]  81.12M  77.4MB/s    in 1.0s    

2020-04-29 15:29:24 (77.4 MB/s) - ‘Miniconda3-py37_4.8.2-Linux-x86_64.sh’ saved [85055499/85055499]

PREFIX=/usr/local
Unpacking payload ...
Solving environment: - done

## Package Plan ##

  environment location: /usr/local

  added / updated specs:
    - _libgcc_mutex==0.1=main
    - asn1crypto==1.3.0=py37_0
    - ca-certificates==2020.1.1=0
    - certifi==2019.11.28=py37_0
    - cffi==1.14.0=py37h2e261b9_0
    - chardet==3.0.4=py37_1003
    - conda-package-handling==1.6.0=py37h7b6

In [0]:
#@title Check conda / GPU are working
!conda info --envs
!nvidia-smi

# conda environments:
#
base                  *  /usr/local

Wed Apr 29 15:29:56 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64.00    Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   30C    P0    25W / 250W |      0MiB / 16280MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:               

In [0]:
#@title Clone git

%cd "/content/"
!git clone https://github.com/harskish/ganspace
%cd ganspace

/content
Cloning into 'ganspace'...
remote: Enumerating objects: 61, done.
remote: Counting objects: 100% (61/61), done.
remote: Compressing objects: 100% (47/47), done.
remote: Total 193 (delta 26), reused 30 (delta 14), pack-reused 132
Receiving objects: 100% (193/193), 15.64 MiB | 17.35 MiB/s, done.
Resolving deltas: 100% (36/36), done.
/content/ganspace


In [0]:
#@title Overwrite environment.yml
%%writefile environment.yml
name: base
channels:
  - defaults
  - conda-forge
  - pytorch
dependencies:
  - python=3.7
  - pytorch::pytorch=1.3
  - pytorch::torchvision
  - cudatoolkit=10.1
  - pillow=6.2
  - ffmpeg
  - tqdm
  - scikit-learn
  - scikit-image
  - boto3
  - requests
  - nltk
  - pip
  - pip:
    - fbpca
    - pyopengltk

# conda env update -f environment.yml --prune


Overwriting environment.yml


In [0]:
#@title Install remaining packages
!conda env update -f environment.yml --prune
!git submodule update --init --recursive
!python -c "import nltk; nltk.download('wordnet')"
!wget https://files.pythonhosted.org/packages/5e/3f/5658c38579b41866ba21ee1b5020b8225cec86fe717e4b1c5c972de0a33c/pycuda-2019.1.2.tar.gz
!tar -xzf pycuda-2019.1.2.tar.gz
%cd /content/ganspace/pycuda-2019.1.2
!python configure.py --cuda-enable-gl --cuda-root=/usr/local/cuda
!make install
%cd "/content/ganspace"
%pip install setuptools cython glumpy ipykernel
%cd models/stylegan2/stylegan2-pytorch/op
!python -c "import torch; import upfirdn2d_op; import fused; print('OK')"
!python setup.py install
%cd "/content/ganspace"

Streaming output truncated to the last 5000 lines.
     explicit shared_ptr(std::auto_ptr<Y> & r): px(r.get()), pn()
                              ^~~~~~~~
In file included from /usr/include/c++/7/memory:80:0,
                 from bpl-subset/bpl_subset/boost/config/no_tr1/memory.hpp:21,
                 from bpl-subset/bpl_subset/boost/get_pointer.hpp:12,
                 from bpl-subset/bpl_subset/boost/python/object/pointer_holder.hpp:11,
                 from bpl-subset/bpl_subset/boost/python/to_python_indirect.hpp:10,
                 from bpl-subset/bpl_subset/boost/python/converter/arg_to_python.hpp:10,
                 from bpl-subset/bpl_subset/boost/python/call.hpp:15,
                 from bpl-subset/bpl_subset/boost/python/object_core.hpp:14,
                 from bpl-subset/bpl_subset/boost/python/object.hpp:9,
                 from bpl-subset/bpl_subset/boost/python/scope.hpp:9,
                 from bpl-subset/bpl_subset/libs/python/src/module.cpp:9:
/usr/include/c++/7/

# Convert model weights

1. Git clone Tensorflow Stylegan
2. install correct TF version (you may have to restart the runtime)
3. Use convert weights script in ganspace directory to convert to a pytorch model

(skip this step if you already have a pytorch model)

In [0]:
%cd "/content"
!git clone https://github.com/skyflynil/stylegan2
%cd ganspace

/content
Cloning into 'stylegan2'...
remote: Enumerating objects: 93, done.
remote: Total 93 (delta 0), reused 0 (delta 0), pack-reused 93
Unpacking objects: 100% (93/93), done.


In [0]:
%pip install tensorflow-gpu==1.15 tensorboard

     |████████████████████████████████| 3.0 MB 104 kB/s 
     |████████████████████████████████| 89 kB 6.7 MB/s 
     |████████████████████████████████| 777 kB 28.8 MB/s 
     |████████████████████████████████| 155 kB 67.1 MB/s 
     |████████████████████████████████| 147 kB 71.6 MB/s 
     |████████████████████████████████| 77 kB 7.4 MB/s 
ERROR: tensorflow 1.15.0 requires tensorflow-estimator==1.15.1, which is not installed.
ERROR: tensorflow 1.15.0 has requirement tensorboard<1.16.0,>=1.15.0, but you'll have tensorboard 2.2.1 which is incompatible.


The convert weight script takes two arguments: 

```

--repo - Path to tensorflow stylegan2 repo
       - Path to your model

```



In [0]:
!python /content/ganspace/models/stylegan2/stylegan2-pytorch/convert_weight.py --repo="/content/drive/My Drive/ML/stylegan2" "/content/drive/My Drive/ML/stylegan_models/stylegan2-ffhq-config-f.pkl" #convert weights

Streaming output truncated to the last 5000 lines.
   [-1.61227202e+00  1.55068862e+00 -3.92967254e-01 ...  1.16954684e+00
     2.20582628e+00  6.44302487e-01]
   [-1.07039320e+00 -3.02256733e-01 -2.24108362e+00 ...  9.73994434e-01
    -3.05091429e+00  1.50675607e+00]
   [-5.56087375e-01  1.05091488e+00  2.33004117e+00 ...  2.60009050e+00
    -2.71971083e+00  5.14869869e-01]]]


 [[[ 5.20571470e-02 -5.40668106e+00 -7.36662567e-01 ...  2.21799564e+00
     2.56278586e+00  1.25093687e+00]
   [-8.99886265e-02 -9.04133976e-01 -1.18445873e+00 ...  1.67408895e+00
     3.05204010e+00  6.80284619e-01]
   [ 1.10533595e-01 -2.94884133e+00 -1.09510720e+00 ... -9.92243886e-01
     2.90932465e+00 -2.67373659e-02]
   ...
   [ 5.79441369e-01 -1.30697536e+00 -1.61252761e+00 ...  1.34024203e+00
     3.84756178e-01  9.49442208e-01]
   [-1.75052762e+00  2.55677748e+00 -2.80922079e+00 ...  6.74462378e-01
    -1.02041709e+00  2.96222568e-01]
   [-2.64245701e+00 -1.91694692e-01 -1.66388118e+00 ...  9.1049218

In [0]:
!cp "/content/ganspace/stylegan2-ffhq-config-f.pt" "/content/drive/My Drive/" #copy pytorch model to your drive

# Run PCA Analysis

From here, open models/wrappers.py, and edit the stylegan2 configs dict on line 110 to include your model and its corresponding resolution.

I.E from

        # Image widths
        configs = {
            # Converted NVIDIA official
            'ffhq': 1024,
            'car': 512,
            'cat': 256,
            'church': 256,
            'horse': 256,
            # Tuomas
            'bedrooms': 256,
            'kitchen': 256,
            'places': 256,
        }

to 

        # Image widths
        configs = {
            # Converted NVIDIA official
            'your_model': your_resolution,
            'ffhq': 1024,
            'car': 512,
            'cat': 256,
            'church': 256,
            'horse': 256,
            # Tuomas
            'bedrooms': 256,
            'kitchen': 256,
            'places': 256,
        }

Then copy your pytorch model over to your drive account or any other hosting platform, and add the direct download link to the checkpoints dict in the download_checkpoint function on line 136.

    def download_checkpoint(self, outfile):
        checkpoints = { 'yourmodel': 'https://drive.google.com/yourmodel',
            'horse': 'https://drive.google.com/uc?export=download&id=18SkqWAkgt0fIwDEf2pqeaenNi4OoCo-0',
            'ffhq': 'https://drive.google.com/uc?id=12yYXZymadSIj74Yue1Q7RrlbIqrXggo3',
            'church': 'https://drive.google.com/uc?export=download&id=1HFM694112b_im01JT7wop0faftw9ty5g',
            'car': 'https://drive.google.com/uc?export=download&id=1iRoWclWVbDBAy5iXYZrQnKYSbZUqXI6y',
            'cat': 'https://drive.google.com/uc?export=download&id=15vJP8GDr0FlRYpE8gD7CdeEz2mXrQMgN',
            'places': 'https://drive.google.com/uc?export=download&id=1X8-wIH3aYKjgDZt4KMOtQzN1m4AlCVhm',
            'bedrooms': 'https://drive.google.com/uc?export=download&id=1nZTW7mjazs-qPhkmbsOLLA_6qws-eNQu',
            'kitchen': 'https://drive.google.com/uc?export=download&id=15dCpnZ1YLAnETAPB0FGmXwdBclbwMEkZ'
        }




#Options


```
Command line paramaters:
  --model      one of [ProGAN, BigGAN-512, BigGAN-256, BigGAN-128, StyleGAN, StyleGAN2]
  --class      class name; leave empty to list options
  --layer      layer at which to perform PCA; leave empty to list options
  --use_w      treat W as the main latent space (StyleGAN / StyleGAN2)
  --inputs     load previously exported edits from directory
  --sigma      number of stdevs to use in visualize.py
  -n           number of PCA samples
  -b           override automatic minibatch size detection
  -c           number of components to keep

```




In [0]:
model = 'StyleGAN2' 
model_class = 'ffhq' #this is the name of your model in the configs
num_components = 80

In [0]:
#@title Check layers available for analysis
!python visualize.py --model $model --class $model_class --use_w

[29.04 15:55] StyleGAN2, g_mapping, ipca
Layer 'g_mapping' not found in model!
Available layers: 
style
style.0
style.1
style.2
style.3
style.4
style.5
style.6
style.7
style.8
input
conv1
conv1.conv
conv1.conv.modulation
conv1.noise
conv1.activate
to_rgb1
to_rgb1.conv
to_rgb1.conv.modulation
convs
convs.0
convs.0.conv
convs.0.conv.blur
convs.0.conv.modulation
convs.0.noise
convs.0.activate
convs.1
convs.1.conv
convs.1.conv.modulation
convs.1.noise
convs.1.activate
convs.2
convs.2.conv
convs.2.conv.blur
convs.2.conv.modulation
convs.2.noise
convs.2.activate
convs.3
convs.3.conv
convs.3.conv.modulation
convs.3.noise
convs.3.activate
convs.4
convs.4.conv
convs.4.conv.blur
convs.4.conv.modulation
convs.4.noise
convs.4.activate
convs.5
convs.5.conv
convs.5.conv.modulation
convs.5.noise
convs.5.activate
convs.6
convs.6.conv
convs.6.conv.blur
convs.6.conv.modulation
convs.6.noise
convs.6.activate
convs.7
convs.7.conv
convs.7.conv.modulation
convs.7.noise
convs.7.activate
convs.8
convs.8.conv


In [0]:
!python visualize.py --model $model --class $model_class --use_w --layer=style -c $num_components

[29.04 15:58] StyleGAN2, style, ipca
Feature shape: torch.Size([1, 512])
Not cached
[29.04 15:58] Computing stylegan2-ffhq_style_ipca_c80_n300000_w.npz
Reusing InstrumentedModel instance
Using W latent space
Feature shape: torch.Size([1, 512])
B=20, N=300000, dims=512, N/dims=585.9
Sampling latents: 100% 15100/15100 [00:27<00:00, 557.86it/s]
Fitting batches (NB=2000): 100% 150/150 [00:30<00:00,  4.92it/s]
Total time: 0:00:58.062044
Batch size 2: memory usage 10071MB
Batch size: 2
[29.04 15:59] Creating visualizations
Sparsity: 0.00
Figure(1400x1200)
Figure(1400x1200)
Random images:   0% 0/10 [00:00<?, ?it/s]Figure(1400x1200)
Random images:  10% 1/10 [00:09<01:28,  9.86s/it]Figure(1400x1200)
Random images:  20% 2/10 [00:18<01:16,  9.58s/it]Figure(1400x1200)
Random images:  30% 3/10 [00:27<01:05,  9.37s/it]Figure(1400x1200)
Random images:  40% 4/10 [00:36<00:55,  9.28s/it]Figure(1400x1200)
Random images:  50% 5/10 [00:45<00:45,  9.16s/it]Figure(1400x1200)
Random images:  60% 6/10 [00:54<

In [0]:
!python visualize.py --model=$model --class=$model_class --use_w --layer="style" -b=500 --batch --video #add -video to generate videos

In [0]:
!zip -r samples.zip "/content/ganspace/out/StyleGAN2-ffhq" #zip up samples for download

In [0]:
%cp -r "/content/ganspace/cache/components" "/content/drive/My Drive/ML/stylegan2/comps" #copying components over to google drive

# Explore Directions!

After running visualize.py, your components will be stored in an npz file in /content/ganspace/cache/components/ - below the npz file is unpacked, and a component/direction is chosen at random. 

Using the UI, you can explore the latent direction and give it a name, which will be appeneded to the named_directions dictionary and saved as 'direction_name.npy' for later use.

From here, you may want to copy the components over to your drive, factory reset the notebook and reinstall tensorflow. I'm getting some errors with conflicting versions.


In [0]:
path_to_tf_stylegan = '/content/drive/My Drive/ML/stylegan2'
path_to_model = '/content/drive/My Drive/ML/stylegan_models/stylegan2-ffhq-config-f.pkl'
path_to_components = '/content/drive/My Drive/ML/stylegan2/components/stylegan2-ffhq_style_ipca_c80_n300000_w.npz'
named_directions = {} #init named_directions dict to save directions

In [0]:
#@title Load model
%pip install tensorflow-gpu==1.15
%cd $path_to_tf_stylegan
import tensorflow as tf
import ipywidgets as widgets
import pretrained_networks
import PIL.Image
import numpy as np
import argparse
import numpy as np
import PIL.Image
import dnnlib
import dnnlib.tflib as tflib
import re
import sys
from io import BytesIO
import IPython.display
import numpy as np
from math import ceil
from PIL import Image, ImageDraw
import imageio
import pretrained_networks

src_model = path_to_model

_G, _D, Gs = pretrained_networks.load_networks(src_model)
Gs_syn_kwargs = dnnlib.EasyDict()
batch_size = 1
Gs_syn_kwargs.output_transform = dict(func=tflib.convert_images_to_uint8, nchw_to_nhwc=True)
Gs_syn_kwargs.randomize_noise = True
Gs_syn_kwargs.minibatch_size = batch_size

noise_vars = [var for name, var in Gs.components.synthesis.vars.items() if name.startswith('noise')]

Streaming output truncated to the last 5000 lines.
   [-1.61227202e+00  1.55068862e+00 -3.92967254e-01 ...  1.16954684e+00
     2.20582628e+00  6.44302487e-01]
   [-1.07039320e+00 -3.02256733e-01 -2.24108362e+00 ...  9.73994434e-01
    -3.05091429e+00  1.50675607e+00]
   [-5.56087375e-01  1.05091488e+00  2.33004117e+00 ...  2.60009050e+00
    -2.71971083e+00  5.14869869e-01]]]


 [[[ 5.20571470e-02 -5.40668106e+00 -7.36662567e-01 ...  2.21799564e+00
     2.56278586e+00  1.25093687e+00]
   [-8.99886265e-02 -9.04133976e-01 -1.18445873e+00 ...  1.67408895e+00
     3.05204010e+00  6.80284619e-01]
   [ 1.10533595e-01 -2.94884133e+00 -1.09510720e+00 ... -9.92243886e-01
     2.90932465e+00 -2.67373659e-02]
   ...
   [ 5.79441369e-01 -1.30697536e+00 -1.61252761e+00 ...  1.34024203e+00
     3.84756178e-01  9.49442208e-01]
   [-1.75052762e+00  2.55677748e+00 -2.80922079e+00 ...  6.74462378e-01
    -1.02041709e+00  2.96222568e-01]
   [-2.64245701e+00 -1.91694692e-01 -1.66388118e+00 ...  9.1049218

In [27]:
#@title Load a component at random

comps = np.load(path_to_components)
lst = comps.files
latent_dirs = []
latent_stdevs = []

load_activations = True

for item in lst:
    # loading latent directions
    # TODO: what is the difference btwn act_comp and latent_comp? should I use one, the other or both?

    # print('\n')
    # print('--------'*10)
    # print(item)
    if load_activations:
      if item == 'act_comp':
        # print(comps[item].shape[0])
        for i in range(comps[item].shape[0]):
          # print(comps[item][i].shape)
          latent_dirs.append(comps[item][i])
      if item == 'act_stdev':
        # print()
        for i in range(comps[item].shape[0]):
          latent_stdevs.append(comps[item][i])
    else:
      if item == 'lat_comp':
        # print(comps[item].shape[0])
        for i in range(comps[item].shape[0]):
          # print(comps[item][i].shape)
          latent_dirs.append(comps[item][i])
      if item == 'lat_stdev':
        # print()
        for i in range(comps[item].shape[0]):
          latent_stdevs.append(comps[item][i])
        
    # print('--------'*10)
    # print('\n')
    

#load one at random 
num = np.random.randint(num_components)
if num in named_directions.values():
  print(f'Direction already named: {list(named_directions.keys())[list(named_directions.values()).index(num)]}')

random_dir = latent_dirs[num]
random_dir_stdev = latent_dirs[num]

random_dir = np.expand_dims(random_dir, axis=0)
#TODO: I think currently this will only work for 1024x1024 models make this adjustable
random_dir = np.tile(random_dir, [1, 18, 1]) 

print(f'Loaded Component No. {num}')


Loaded Component No. 37


In [28]:
#@title Run UI
from IPython.utils import io

def name_direction(sender):
  if num in named_directions.values():
    target_key = list(named_directions.keys())[list(named_directions.values()).index(num)]
    print(f'Direction already named: {target_key}')
    print(f'Overwriting... ')
    del(named_directions[target_key])
  named_directions[text.value] = num
  save_direction(random_dir, text.value)
  for item in named_directions:
    print(item, named_directions[item])

def save_direction(direction, filename):
  filename += ".npy"
  np.save(filename, direction, allow_pickle=True, fix_imports=True)
  print(f'Latent direction saved as {filename}')

# Taken from https://github.com/alexanderkuk/log-progress
def log_progress(sequence, every=1, size=None, name='Items'):
    from ipywidgets import IntProgress, HTML, VBox
    from IPython.display import display

    is_iterator = False
    if size is None:
        try:
            size = len(sequence)
        except TypeError:
            is_iterator = True
    if size is not None:
        if every is None:
            if size <= 200:
                every = 1
            else:
                every = int(size / 200)     # every 0.5%
    else:
        assert every is not None, 'sequence is iterator, set every'

    if is_iterator:
        progress = IntProgress(min=0, max=1, value=1)
        progress.bar_style = 'info'
    else:
        progress = IntProgress(min=0, max=size, value=0)
    label = HTML()
    box = VBox(children=[label, progress])
    display(box)

    index = 0
    try:
        for index, record in enumerate(sequence, 1):
            if index == 1 or index % every == 0:
                if is_iterator:
                    label.value = '{name}: {index} / ?'.format(
                        name=name,
                        index=index
                    )
                else:
                    progress.value = index
                    label.value = u'{name}: {index} / {size}'.format(
                        name=name,
                        index=index,
                        size=size
                    )
            yield record
    except:
        progress.bar_style = 'danger'
        raise
    else:
        progress.bar_style = 'success'
        progress.value = index
        label.value = "{name}: {index}".format(
            name=name,
            index=str(index or '?')
        )

def generate_mov(seed, truncation, direction_vec, scale, n_frames, out_name = 'out', noise_spec = None, loop=True):
  """Generates a mov moving back and forth along the chosen direction vector"""
  # Example of reading a generated set of images, and storing as MP4.
  %mkdir out
  movieName = f'out/{out_name}.mp4'
  offset = -10
  step = 20 / n_frames
  imgs = []
  for i in range(n_frames):
    print(f'{i} / {n_frames}')
    Gs_kwargs = dnnlib.EasyDict()
    Gs_kwargs.output_transform = dict(func=tflib.convert_images_to_uint8, nchw_to_nhwc=True)
    Gs_kwargs.randomize_noise = False
    if truncation is not None:
        Gs_kwargs.truncation_psi = truncation
            
    rnd = np.random.RandomState(seed)
        
    if noise_spec is None:
      tflib.set_vars({var: rnd.randn(*var.shape.as_list()) for var in noise_vars}) # [height, width]
    else:
      tflib.set_vars(noise_spec)
    
    batch_size = 1
    all_seeds = [seed] * batch_size
    all_z = np.stack([np.random.RandomState(seed).randn(*Gs.input_shape[1:]) for seed in all_seeds]) # [minibatch, component]
    all_w = Gs.components.mapping.run(all_z, None) # [minibatch, layer, component]
    if truncation != 1:
        w_avg = Gs.get_var('dlatent_avg')
        all_w = w_avg + (all_w - w_avg) * truncation # [minibatch, layer, component]
    all_w += direction_vec * offset * scale
    all_images = Gs.components.synthesis.run(all_w, **Gs_syn_kwargs)
    #save image and display
    final_im = PIL.Image.fromarray(np.median(all_images, axis=0).astype(np.uint8))
    imgs.append(final_im)
    #increase offset
    offset += step
  if loop:
    imgs += imgs[::-1]
  with imageio.get_writer(movieName, mode='I') as writer:
    for image in log_progress(list(imgs), name = "Creating animation"):
        writer.append_data(np.array(image))

def display_sample(seed, truncation, distance, scale, disp=True, save=None, noise_spec=None):
    # blockPrint()
    with io.capture_output() as captured:
      # weighted_average(Gs, Gsd, blending)
      
      Gs_kwargs = dnnlib.EasyDict()
      Gs_kwargs.output_transform = dict(func=tflib.convert_images_to_uint8, nchw_to_nhwc=True)
      Gs_kwargs.randomize_noise = False
      if truncation is not None:
          Gs_kwargs.truncation_psi = truncation
          
      rnd = np.random.RandomState(seed)
      
      if noise_spec is None:
        tflib.set_vars({var: rnd.randn(*var.shape.as_list()) for var in noise_vars}) # [height, width]
      else:
        tflib.set_vars(noise_spec)
      
      batch_size = 1
      all_seeds = [seed] * batch_size
      all_z = np.stack([np.random.RandomState(seed).randn(*Gs.input_shape[1:]) for seed in all_seeds]) # [minibatch, component]
      all_w = Gs.components.mapping.run(all_z, None) # [minibatch, layer, component]
      if truncation != 1:
          w_avg = Gs.get_var('dlatent_avg')
          all_w = w_avg + (all_w - w_avg) * truncation # [minibatch, layer, component]
      all_w += random_dir * distance * scale
      all_images = Gs.components.synthesis.run(all_w, **Gs_syn_kwargs)
      #save image and display
      final_im = PIL.Image.fromarray(np.median(all_images, axis=0).astype(np.uint8))
    if disp:
      display(final_im)
    if save is not None:
      if disp == False:
        print(save)
      final_im.save(f'out/{seed}_{save:05}.png')

seed = np.random.randint(0,100000)
style = {'description_width': 'initial'}

seed = widgets.IntSlider(min=0, max=100000, step=1, value=seed, description='Seed: ', continuous_update=False)
truncation = widgets.FloatSlider(min=-2, max=2, step=0.1, value=0.7, description='Truncation: ', continuous_update=False)
distance = widgets.FloatSlider(min=-10, max=10, step=0.1, value=0, description='Distance: ', continuous_update=False, style=style)
scale = widgets.FloatSlider(min=0, max=5, step=0.05, value=1, description='Scale: ', continuous_update=False)
text = widgets.Text(description="Name component here", style=style, width=200)

bot_box = widgets.HBox([seed, truncation, distance, scale, text])
ui = widgets.VBox([bot_box])

out = widgets.interactive_output(display_sample, {'seed': seed, 'truncation': truncation, 'distance': distance, 'scale': scale})

display(ui, out)
text.on_submit(name_direction)




Output()

In [0]:
#script to generate a movie with direction

direction_name = 'age'
loc = named_directions[direction_name]

generate_mov(seed = 1000, truncation = 0.8, direction_vec = latent_dirs[loc], scale = 1, n_frames = 100, out_name = direction_name, loop=True)

In [0]:
#@title Select from named directions

from IPython.display import display, clear_output

vardict = list(named_directions.keys())
select_variable = widgets.Dropdown(
    options=vardict,
    value=vardict[0],
    description='Select variable:',
    disabled=False,
    button_style=''
)

def set_direction(b):
    clear_output()
    print(select_variable.value)
    random_dir = latent_dirs[named_directions[select_variable.value]]
    seed = np.random.randint(0,100000)
    style = {'description_width': 'initial'}

    seed = widgets.IntSlider(min=0, max=100000, step=1, value=seed, description='Seed: ', continuous_update=False)
    truncation = widgets.FloatSlider(min=-2, max=2, step=0.1, value=0.7, description='Truncation: ', continuous_update=False)
    distance = widgets.FloatSlider(min=-10, max=10, step=0.1, value=0, description='Distance: ', continuous_update=False, style=style)
    scale = widgets.FloatSlider(min=0, max=5, step=0.05, value=1, description='Scale: ', continuous_update=False)

    bot_box = widgets.HBox([seed, truncation, distance, scale])
    ui = widgets.VBox([bot_box])

    out = widgets.interactive_output(display_sample, {'seed': seed, 'truncation': truncation, 'distance': distance, 'scale': scale})
    display(select_variable)
    display(ui, out)

random_dir = latent_dirs[named_directions[select_variable.value]]
seed = np.random.randint(0,100000)
style = {'description_width': 'initial'}

seed = widgets.IntSlider(min=0, max=100000, step=1, value=seed, description='Seed: ', continuous_update=False)
truncation = widgets.FloatSlider(min=-2, max=2, step=0.1, value=0.7, description='Truncation: ', continuous_update=False)
distance = widgets.FloatSlider(min=-10, max=10, step=0.1, value=0, description='Distance: ', continuous_update=False, style=style)
scale = widgets.FloatSlider(min=0, max=5, step=0.05, value=1, description='Scale: ', continuous_update=False)

bot_box = widgets.HBox([seed, truncation, distance, scale])
ui = widgets.VBox([bot_box])

out = widgets.interactive_output(display_sample, {'seed': seed, 'truncation': truncation, 'distance': distance, 'scale': scale})

display(select_variable)

select_variable.observe(set_direction, names='value')



smile


Dropdown(description='Select variable:', index=2, options=('age', 'gender', 'smile'), value='smile')

Output()